In [1]:
from collections import deque, defaultdict
import numpy as np
import math
from typing import Optional

In [2]:
class Monkey():
    def __init__(
        self,
        monkey_id: int,
        starting_items: deque[int],
        operator,
        ops: tuple[Optional[int], Optional[int]],
        divisible: int,
        true_next_monkey: int,
        false_next_monkey: int
    ) -> None:
        self.monkey_id = monkey_id
        self.items = starting_items
        self.operator = operator
        self.ops = ops
        self.divisible = divisible
        self.true_next_monkey = true_next_monkey
        self.false_next_monkey = false_next_monkey
        self.kgv = None
    
    def __repr__(self):
        return f"Monkey {self.monkey_id}, {self.items}, {self.ops}, {self.divisible}, {self.true_next_monkey}/{self.false_next_monkey}"
    
    def __call__(self, old_val):
        ops = []
        def _add_to_op(idx):
            if self.ops[idx] is None:
                ops.append(old_val)
            else:
                ops.append(self.ops[idx])
        for idx in range(len(self.ops)):
            _add_to_op(idx)

        ret_val = self.operator(ops)
        if self.lcm is not None:
            ret_val = ret_val % self.lcm
        return ret_val
    
    def set_lcm_val(self, val: int):
        self.lcm = val 

In [3]:
def parse_monkey_input(input_iter):
    monkeys = []

    while True:
        try:
            monkey_id = int(next(input_iter).rstrip().split(" ")[-1][:-1])
            starting_items = deque([
                int(score)
                for score in next(input_iter).rstrip()[18:].split(", ")
            ])
            operation_row = next(input_iter).rstrip()[19:].split(" ")
            if operation_row[1] == "+":
                operator = np.sum
            elif operation_row[1] == "*":
                operator = np.prod
            else:
                raise NotImplementedError(operation_row)
            lhs_op = None if operation_row[0] == "old" else int(operation_row[0])
            rhs_op = None if operation_row[2] == "old" else int(operation_row[2])
            
            divisible = int(next(input_iter).rstrip().split(" ")[-1])
            true_next_monkey = int(next(input_iter).rstrip().split(" ")[-1])
            false_next_monkey = int(next(input_iter).rstrip()[-1].split(" ")[-1])

            monkeys.append(Monkey(
                monkey_id=monkey_id,
                starting_items=starting_items,
                operator=operator,
                ops=(lhs_op, rhs_op),
                divisible=divisible,
                true_next_monkey=true_next_monkey,
                false_next_monkey=false_next_monkey,
            ))
            next(input_iter)

        except StopIteration:
            break
    return monkeys

In [4]:
def simulate_monkeys(monkeys: list[Monkey], num_rounds: int, div_by_three: bool = False) -> None:
    if not div_by_three:
        monkey_div = [monkey.divisible for monkey in monkeys]
        lcm = math.lcm(*monkey_div)
        for monkey in monkeys:
            monkey.set_lcm_val(lcm)
    
    activity_dict = defaultdict(int)
    for round_idx in range(num_rounds):
        for monkey in monkeys:
            while(monkey.items):
                activity_dict[monkey.monkey_id] += 1
                item = monkey.items.popleft()
                item = monkey(item)
                if div_by_three:
                    item = item // 3
                if item % monkey.divisible:
                    monkeys[monkey.false_next_monkey].items.append(item)
                else:
                    monkeys[monkey.true_next_monkey].items.append(item)

        print(f"After round {round_idx}, the monkeys are holding items with these worry levels:")
        for monkey in monkeys:
            print(f"Monkey {monkey.monkey_id}: {', '.join(map(str, monkey.items))}")
        print()
    
    for monkey_idx, activity in activity_dict.items():
        print(f"Monkey {monkey_idx} inspected items {activity} times.")
    
    monkey_business = np.prod(sorted(activity_dict.values())[-2:])
    print(f"Monkey Business: {monkey_business}")

In [5]:
monkeys = parse_monkey_input(open("test_input.txt"))
simulate_monkeys(monkeys, 20)

After round 0, the monkeys are holding items with these worry levels:
Monkey 0: 60, 71, 81, 80
Monkey 1: 77, 1504, 1865, 6244, 3603, 9412
Monkey 2: 
Monkey 3: 

After round 1, the monkeys are holding items with these worry levels:
Monkey 0: 83, 1510, 1871, 6250, 3609, 9418
Monkey 1: 1143, 1352, 1542, 1523
Monkey 2: 
Monkey 3: 

After round 2, the monkeys are holding items with these worry levels:
Monkey 0: 1149, 1358, 1548, 1529
Monkey 1: 1580, 28693, 35552, 22176, 68574, 82368
Monkey 2: 
Monkey 3: 

After round 3, the monkeys are holding items with these worry levels:
Monkey 0: 1586, 28699, 35558, 22182, 68580, 82374
Monkey 1: 21834, 25805, 29415, 29054
Monkey 2: 
Monkey 3: 

After round 4, the monkeys are holding items with these worry levels:
Monkey 0: 21840, 25811, 29421, 29060
Monkey 1: 30137, 62399, 35153, 47522, 19877, 94395
Monkey 2: 
Monkey 3: 

After round 5, the monkeys are holding items with these worry levels:
Monkey 0: 30143, 62405, 35159, 47528, 19883, 94401, 69258
Monke

In [6]:
monkeys = parse_monkey_input(open("felix_input.txt"))
simulate_monkeys(monkeys, 20)

After round 0, the monkeys are holding items with these worry levels:
Monkey 0: 63, 85, 73, 69, 79, 9409, 7396
Monkey 1: 56
Monkey 2: 
Monkey 3: 85
Monkey 4: 21131, 84, 81, 79, 82, 83, 1244, 1108, 1176, 1108, 870, 1465, 1567, 1771, 19196, 24041, 27917, 1703, 1023, 77, 90, 105, 101, 90, 92, 66, 71
Monkey 5: 
Monkey 6: 
Monkey 7: 

After round 1, the monkeys are holding items with these worry levels:
Monkey 0: 57, 7225
Monkey 1: 21137, 90, 87, 85, 88, 89, 1250, 1114, 1182, 1114, 876, 1471, 1777, 19202, 24047, 27923, 1709, 1029, 83, 96, 111, 107, 96, 98, 72, 77
Monkey 2: 
Monkey 3: 1573
Monkey 4: 27594, 23718, 22426, 25656, 3039246, 2389047, 1205
Monkey 5: 
Monkey 6: 
Monkey 7: 

After round 2, the monkeys are holding items with these worry levels:
Monkey 0: 91, 89, 1251, 1115, 1183, 1115, 877, 19203, 97, 97, 99, 73, 2474329
Monkey 1: 27600, 23724, 22432, 3039252, 2389053, 1211
Monkey 2: 
Monkey 3: 25662
Monkey 4: 18550, 2333814, 359485, 1635, 1601, 1669, 25163, 408955, 474847, 29209, 176

In [7]:
monkeys = parse_monkey_input(open("test_input.txt"))
simulate_monkeys(monkeys, 10000, div_by_three=False)

After round 0, the monkeys are holding items with these worry levels:
Monkey 0: 60, 71, 81, 80
Monkey 1: 77, 1504, 1865, 6244, 3603, 9412
Monkey 2: 
Monkey 3: 

After round 1, the monkeys are holding items with these worry levels:
Monkey 0: 83, 1510, 1871, 6250, 3609, 9418
Monkey 1: 1143, 1352, 1542, 1523
Monkey 2: 
Monkey 3: 

After round 2, the monkeys are holding items with these worry levels:
Monkey 0: 1149, 1358, 1548, 1529
Monkey 1: 1580, 28693, 35552, 22176, 68574, 82368
Monkey 2: 
Monkey 3: 

After round 3, the monkeys are holding items with these worry levels:
Monkey 0: 1586, 28699, 35558, 22182, 68580, 82374
Monkey 1: 21834, 25805, 29415, 29054
Monkey 2: 
Monkey 3: 

After round 4, the monkeys are holding items with these worry levels:
Monkey 0: 21840, 25811, 29421, 29060
Monkey 1: 30137, 62399, 35153, 47522, 19877, 94395
Monkey 2: 
Monkey 3: 

After round 5, the monkeys are holding items with these worry levels:
Monkey 0: 30143, 62405, 35159, 47528, 19883, 94401, 69258
Monke

In [8]:
monkeys = parse_monkey_input(open("felix_input.txt"))
simulate_monkeys(monkeys, 10000, div_by_three=False)

After round 0, the monkeys are holding items with these worry levels:
Monkey 0: 63, 85, 73, 69, 79, 9409, 7396
Monkey 1: 56
Monkey 2: 
Monkey 3: 85
Monkey 4: 21131, 84, 81, 79, 82, 83, 1244, 1108, 1176, 1108, 870, 1465, 1567, 1771, 19196, 24041, 27917, 1703, 1023, 77, 90, 105, 101, 90, 92, 66, 71
Monkey 5: 
Monkey 6: 
Monkey 7: 

After round 1, the monkeys are holding items with these worry levels:
Monkey 0: 57, 7225
Monkey 1: 21137, 90, 87, 85, 88, 89, 1250, 1114, 1182, 1114, 876, 1471, 1777, 19202, 24047, 27923, 1709, 1029, 83, 96, 111, 107, 96, 98, 72, 77
Monkey 2: 
Monkey 3: 1573
Monkey 4: 27594, 23718, 22426, 25656, 3039246, 2389047, 1205
Monkey 5: 
Monkey 6: 
Monkey 7: 

After round 2, the monkeys are holding items with these worry levels:
Monkey 0: 91, 89, 1251, 1115, 1183, 1115, 877, 19203, 97, 97, 99, 73, 2474329
Monkey 1: 27600, 23724, 22432, 3039252, 2389053, 1211
Monkey 2: 
Monkey 3: 25662
Monkey 4: 18550, 2333814, 359485, 1635, 1601, 1669, 25163, 408955, 474847, 29209, 176